# Multi-Task Test
At first we have to install the newest version of gpCAM

In [2]:
##first install the newest version of fvgp
#!pip install gpCAM==8.0.0

## Setup

In [3]:
import numpy as np
import matplotlib.pyplot as plt
from gpcam import fvGPOptimizer
import plotly.graph_objects as go
from itertools import product

%load_ext autoreload
%autoreload 2

## Data

In [4]:
data = np.load("./data/sim_variable_mod.npy")
sparsification = 32

x_data3 = data[:,5:][::sparsification]
y_data3 = data[:,0:3][::sparsification]

#it is good practice to check the format of the data
print(x_data3.shape)
print(y_data3.shape)

(198, 3)
(198, 3)


In [5]:
x = np.linspace(30,100,100)
y = np.linspace(40,130,100)
x_pred3D = np.asarray(list(product(x, y)))
x_pred3D = np.column_stack([x_pred3D, np.zeros((len(x_pred3D),1)) + 300.])

## Plotting

In [6]:
def scatter(x,y,z,size=3, color = 1):
    #if not color: color = z
    fig = go.Figure()
    fig.add_trace(go.Scatter3d(x=x, y=y, z=z,mode='markers',marker=dict(color=color, size = size)))
    
    
    fig.update_layout(autosize=False,
                  width=800, height=800,
                  font=dict(size=18,),
                  margin=dict(l=0, r=0, b=0, t=0))
    fig.show()

In [ ]:
scatter(x_data3[:,0],x_data3[:,1],x_data3[:,2], size = 5, color = y_data3[:,0])
scatter(x_data3[:,0],x_data3[:,1],x_data3[:,2], size = 5, color = y_data3[:,1])
scatter(x_data3[:,0],x_data3[:,1],x_data3[:,2], size = 5, color = y_data3[:,2])

## A simple kernel definition
It is vital in the multi-task case to think hard about kernel design. The kernel is now a function
over $\mathcal{X} \times \mathcal{X} \times T \times T$, where $\mathcal{X}$ is the input and $T$ is the output space. Print the input into kernel, it will have the dimensionality of this cartesian product space. 
The default kernel in fvgp is a deep kernel, which can be good, but there is no guarantee.
To use the default kernel, pytorch has to be installed manually (pip install torch).

In [8]:
#As imple kernel, that won't lead to good performance because its stationary
def mkernel(x1,x2,hps,obj):
    d = obj._get_distance_matrix(x1,x2)
    return hps[0] * obj.matern_kernel_diff1(d,hps[1])

## Initialization

In [9]:
#This is where things get a littlecomplicated. What's with all those numbers there.
#This input space is 3-dimensional, the output space has 3 tasks, but is still 1-dimensional
#in the fvgp world. Therefore fvGP(3,1,3, ...), for 3 dim input, 1 dim output, with 3 outputs 

my_gp2 = fvGPOptimizer(x_data3,y_data3, 1,init_hyperparameters=np.ones((2)), info = True,
              #gp_kernel_function=mkernel #what happens if comment this out? (adjust bounds below)
             )
#change this based on kernel choice
hps_bounds = my_gp2.hps_bounds 
#hps_bounds = np.array([[0.001,10000.],[1.,1000.]])

#my_gp2.update_gp_data(x_data3,y_data3)
print("Global Training in progress")
my_gp2.train(hps_bounds, max_iter = 2)

Global Training in progress
differential_evolution step 1: f(x)= 2346.17
differential_evolution step 2: f(x)= 2324.58


array([ 2.97923504e-01,  2.03701132e+02, -3.12065671e-01,  3.57563676e-01,
        7.14450532e-01,  8.90714997e-01,  9.94907636e-01,  2.84101358e-02,
       -4.18254971e-01,  6.88379654e-01,  8.92109535e-01,  4.79956968e-01,
        4.96193476e-01,  1.18709223e-01,  7.68196011e-01,  9.84582954e-01,
        9.00727752e-01,  2.23402826e-01, -7.02745850e-01, -1.69866944e-01,
       -3.81509363e-02,  7.73736314e-01,  5.76291429e-01, -4.05525031e-02,
        9.61514762e-01,  4.11519937e-02,  3.66534679e-01, -5.05233349e-01,
       -6.20460924e-01,  3.02153081e-01,  5.87527849e-01,  6.30349100e-01,
       -6.10438752e-01, -8.91623333e-01,  7.51695148e-01, -1.25884315e-01,
       -3.73116309e-01,  4.75447466e-01,  8.98253668e-01, -3.68749892e-01,
       -6.81233722e-01,  6.78641184e-01,  7.56089040e-01, -6.64237542e-01,
        9.64682769e-01,  4.99931008e-01,  5.42576091e-01, -3.52717249e-02,
       -6.31393184e-01,  3.73747266e-01,  6.60396865e-01,  7.62478048e-01,
        2.08029123e-01,  

## Prediction

In [9]:
#first task
mean1 = my_gp2.posterior_mean(x_pred3D, x_out = np.zeros((1,1)))["f(x)"]
var1 =  my_gp2.posterior_covariance(x_pred3D, x_out = np.zeros((1,1)))["v(x)"]

#second task
mean2 = my_gp2.posterior_mean(x_pred3D, x_out = np.zeros((1,1)) + 1)["f(x)"]
var2 =  my_gp2.posterior_covariance(x_pred3D, x_out = np.zeros((1,1))+1)["v(x)"]

#third task
mean3 = my_gp2.posterior_mean(x_pred3D, x_out = np.zeros((1,1)) + 2)["f(x)"]
var3 =  my_gp2.posterior_covariance(x_pred3D, x_out = np.zeros((1,1))+2)["v(x)"]

In [10]:
#extract data point to compare to:
index300 = np.where(x_data3[:,2]==300.)
imageX_data = x_data3[index300]
imageY_data = y_data3[index300]
print(y_data3)

[[0.43295063 0.46441413 0.        ]
 [0.40181642 0.49974507 0.        ]
 [0.1870942  0.71756229 0.        ]
 [0.41676125 0.45467055 0.        ]
 [0.44455334 0.43470985 0.        ]
 [0.39230737 0.48049254 0.        ]
 [0.42953228 0.44523945 0.        ]
 [0.1496054  0.79224867 0.        ]
 [0.43262632 0.44393007 0.        ]
 [0.44258668 0.44635835 0.        ]
 [0.47291988 0.41314438 0.        ]
 [0.1720887  0.72290863 0.        ]
 [0.30942105 0.56450971 0.        ]
 [0.23276257 0.64439698 0.        ]
 [0.42880651 0.45937787 0.        ]
 [0.17464414 0.7128479  0.        ]
 [0.16550158 0.73540674 0.        ]
 [0.20867737 0.6463526  0.        ]
 [0.21163248 0.64529777 0.        ]
 [0.20964581 0.65139958 0.        ]
 [0.31421292 0.56284409 0.        ]
 [0.21920471 0.59350833 0.        ]
 [0.2844374  0.58527563 0.        ]
 [0.20957515 0.65478806 0.        ]
 [0.17805    0.65670589 0.        ]
 [0.22776061 0.5513095  0.        ]
 [0.20843044 0.66325407 0.        ]
 [0.23597909 0.55695874 0.  

In [11]:
fig = go.Figure()
fig.add_trace(go.Scatter3d(x=x_pred3D[:,0],y=x_pred3D[:,1], z=mean1,
                             mode='markers',marker=dict(color=mean1, size = 5)))
fig.add_trace(go.Scatter3d(x=imageX_data[:,0], y=imageX_data[:,1] , z=imageY_data[:,0],
                           mode='markers',marker=dict(color=imageY_data[:,0], size = 5)))
fig.update_layout(autosize=False,
                  width=800, height=800,
                  font=dict(size=18,),
                  margin=dict(l=0, r=0, b=0, t=0))
fig.show()



fig = go.Figure()
fig.add_trace(go.Scatter3d(x=x_pred3D[:,0], y=x_pred3D[:,1], z=mean2,
                           mode='markers',marker=dict(color=mean2, size = 5)))
fig.add_trace(go.Scatter3d(x=imageX_data[:,0], y=imageX_data[:,1], z=imageY_data[:,1],
                           mode='markers',marker=dict(color=imageY_data[:,1], size = 5)))
fig.update_layout(autosize=False,
                  width=800, height=800,
                  font=dict(size=18,),
                  margin=dict(l=0, r=0, b=0, t=0))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter3d(x=x_pred3D[:,0], y=x_pred3D[:,1], z=mean3,
                           mode='markers',marker=dict(color=mean3, size = 5)))
fig.add_trace(go.Scatter3d(x=imageX_data[:,0], y=imageX_data[:,1], z=imageY_data[:,2],
                           mode='markers',marker=dict(color=imageY_data[:,2], size = 5)))
fig.update_layout(autosize=False,
                  width=800, height=800,
                  font=dict(size=18,),
                  margin=dict(l=0, r=0, b=0, t=0))
fig.show()



In [ ]:
my_gp2.ask(np.array([[0,1],[0,1],[0,1]]), n = 1, acquisition_function = 'relative information entropy set', x_out = np.array([[0],[1],[2]]), vectorized = True)
my_gp2.ask(np.array([[0,1],[0,1],[0,1]]), n = 1, acquisition_function = 'relative information entropy', x_out = np.array([[0],[1],[2]]), vectorized = True)
my_gp2.ask(np.array([[0,1],[0,1],[0,1]]), n = 1, acquisition_function = 'variance', x_out = np.array([[0],[1],[2]]), vectorized = True)
my_gp2.ask(np.array([[0,1],[0,1],[0,1]]), n = 1, acquisition_function = 'total correlation', x_out = np.array([[0],[1],[2]]), vectorized = True)


my_gp2.ask(np.array([[0,1],[0,1],[0,1]]), n = 4, acquisition_function = 'relative information entropy set', x_out = np.array([[0],[1],[2]]), vectorized = True)
my_gp2.ask(np.array([[0,1],[0,1],[0,1]]), n = 5, acquisition_function = 'relative information entropy', x_out = np.array([[0],[1],[2]]), vectorized = True)
my_gp2.ask(np.array([[0,1],[0,1],[0,1]]), n = 6, acquisition_function = 'variance', x_out = np.array([[0],[1],[2]]), vectorized = True)
my_gp2.ask(np.array([[0,1],[0,1],[0,1]]), n = 2, acquisition_function = 'total correlation', x_out = np.array([[0],[1],[2]]), vectorized = True)

